In [1]:
import numpy as np
import pandas as pd
from scipy.io import loadmat
from skimage import io
import scipy.io as sio
import openpyxl
from openpyxl import load_workbook

import matplotlib
import matplotlib.pyplot as plt

In [2]:
# Put the production-based emissions inventory from Step 1 into Excel for subsequent environmental extended Input-Output (IO) analysis.

In [7]:
fpath = r'D:\02_Python\\01_food_inventory\\'
spec_lst = ["BC", "CO", "NH3", "NOx", "OC", "SO2", "PMOTHR", "NH3-ag"]
fd_lst = ['grain', 'vegetables', 'fruits', 'pig',
          'beef', 'sheep&goat', 'poultry', 'dairy', 'egg']
# load province
pname = pd.read_excel(fpath+r'\data\Sector_names.xlsx',
                      sheet_name='prov_name')
pcname = pd.read_excel(fpath+r'\data\Sector_names.xlsx',
                       sheet_name='prov_name')['name1'].values
ppname = pd.read_excel(fpath+r'\data\Sector_names.xlsx',
                       sheet_name='prov_name')['eng name'].values

sec_name = list(pd.read_excel(fpath+r'\data\Sector_names.xlsx',
                sheet_name='prod_sector').iloc[:, 0])

df = pd.read_excel(fpath+'\data\MRIO_2017_CHN_ag.xlsx',
                   skiprows=[0, 1, 2, 3], header=None)

# emis io inventory

In [3]:
# emis matrix
emis_df = df.iloc[1302+10:1302+21, 3:1305]
emis_df.index = ['BC', 'CO', 'CO2', 'NH3', 'NOx',
                 'OC', 'PM10', 'PM25', 'SO2', 'NH3-ag', 'PMOTHR']

for kk in range(len(spec_lst)):

    # z: Intermediate flow matrix
    z = df.iloc[:-23, 3:1305].values

    # y: final consumption
    y = df.iloc[:-23, 1306:1306+156].values

    # export columns
    ex = df.iloc[:-23, 1306+155].values

    # emis row
    emis = emis_df.loc[spec_lst[kk], :].values

    # total input
    x = z.sum(axis=1) + y.sum(axis=1)

    # a: Direct consumption coefficient matrix
    # f: Diagonalization matrix of emission factors
    a = np.zeros((31*42, 31*42))
    f = np.zeros((31*42))

    for i in range(31*42):
        for j in range(31*42):
            a[i, j] = z[i, j] / x[j]
            f[j] = emis[j] / x[j]

    a[np.isnan(a)] = 0
    f[np.isnan(f)] = 0
    a[np.isinf(a)] = 0
    f[np.isinf(f)] = 0

    # leontief matrix
    I = np.eye(31*42)
    L = np.zeros((31*42, 31*42))
    L = np.linalg.inv(I-a)

    # consumption inventory 1302, 1302
    Flowtmp = np.zeros((31*42, 31*42, 5*31+1))
    for i in range(5*31+1):
        Flowtmp[:, :, i] = np.dot(np.dot(np.diag(f), L), np.diag(y[:, i]))

    # resize matrix: Producer province, production sector, intermediate province, intermediate sector, consumer province, consumer sector
    ssam_new = np.zeros((31, 42, 31, 42, 31, 5))

    for ii in range(31):
        for jj in range(31):
            for mm in range(31):
                ssam_new[ii, :, jj, :, mm, :] = Flowtmp[ii *
                                                        42:(ii+1)*42, jj*42:(jj+1)*42, 5*mm:5*(mm+1)]

    ssam_new[ssam_new < 0] = 0

    sio.savemat(fpath+r'\output\01_csp_inventory\FlowChina_{}.mat'.format(spec_lst[kk]),
                {'{}'.format(spec_lst[kk]): ssam_new})

C:\Users\lionf\anaconda3\envs\liam\lib\site-packages\ipykernel_launcher.py:30: RuntimeWarning: divide by zero encountered in double_scalars
C:\Users\lionf\anaconda3\envs\liam\lib\site-packages\ipykernel_launcher.py:31: RuntimeWarning: divide by zero encountered in double_scalars
C:\Users\lionf\anaconda3\envs\liam\lib\site-packages\ipykernel_launcher.py:30: RuntimeWarning: invalid value encountered in double_scalars
C:\Users\lionf\anaconda3\envs\liam\lib\site-packages\ipykernel_launcher.py:31: RuntimeWarning: invalid value encountered in double_scalars


# money inventory

In [7]:
df = pd.read_excel(fpath+'\data\Copy of China_Multi-Regional_Input-Output_Table_2017.xlsx',
                   skiprows=[0, 1, 2, 3], header=None)

In [ ]:
z = df.iloc[:-23, 3:1305].values

y = df.iloc[:-23, 1306:1306+156].values

x = z.sum(axis=1) + y.sum(axis=1)

a = np.zeros((31*42, 31*42))

for i in range(31*42):
    for j in range(31*42):
        a[i, j] = z[i, j] / x[j]

a[np.isnan(a)] = 0
a[np.isinf(a)] = 0

I = np.eye(31*42)
L = np.zeros((31*42, 31*42))
L = np.linalg.inv(I-a)

Flowtmp = np.zeros((31*42, 31*42, 5*31+1))
for i in range(5*31+1):
    Flowtmp[:, :, i] = np.dot(L, np.diag(y[:, i]))

sio.savemat(fpath+r'\output\01_csp_inventory\FlowChina_traditional.mat',
            {'Flowtmp': Flowtmp})